# Qualitative modelling of farm trajectories in South-Sudanian Burkina Faso

Here is presented a thorough analysis using `ecco` functionalities, with details about the differents results one can get from temporal logic and results visualization.

###### Model computation

In [1]:
# print the execution time
%time
# load the model 
%run -m ecco agsys-2024.rr
# build the State-Transition Graph (STG)
STG = model(_init="Cr+,Fe+") # for the definition of initial states, see main text 
# split initial states (one per scenario)
scenarios = STG.split("INIT")
# print the LBV-model statistics
print(f"The STG has {sum ([len(c) for c in STG])} states encompassing {sum ([len(scenarios[i]) for i in scenarios.isin('INIT')])} scenarios.\n")

CPU times: user 4 µs, sys: 1 µs, total: 5 µs
Wall time: 8.82 µs
The STG has 1444 states encompassing 128 scenarios.



###### Model definition

In [2]:
model.rr

HTML(value="<pre style='font-family:mono;line-height:140%;'><span style='font-weight:bold;color:#008;'>variabl…

###### Defining observables (i.e. farm types)

Farm types definitions can be found in the "Farm types" section and Table 2 (Material and Methods). For more details, see [(Vall et al. 2006, Table 1)](https://agritrop.cirad.fr/530825/1/document_530825.pdf) and [Ouédraogo et al. 2016 (requires a Cirad account)](https://agris.fao.org/agris-search/search.do?recordID=FR2019153347).

In [3]:
# Defining each farm types
A1 = "(~Cc & ~Ca & ~Ma)" 
A2 = "(Cc & ~Ca & ~Ma & Eq & Lv)" 
A3 = "(Cc &  Ca & ~Ma & Eq & Cr & Lv)" 
AP = "(Cc &  Ma & Eq & Cr & Lv)" 
B =  "(~Cc & ~Ca & Ma & Lv)" 

farm_types = {}
farm_types["A1"] = A1 
farm_types["A2"] = A2
farm_types["A3"] = A3
farm_types["AP"] = AP
farm_types["B"] =  B

def fFT(v):
    def f(x) :
        res = ""
        for key,value in farm_types.items():
            if x.name in v.isin(value):
                if res != "":
                    res += ", " 
                res += key
        if res == "":
            res = "various"
        return res
    return f

## Comparing observations and model predictions

Analyses performed in the following are aimed to falsify the model based on empirical observations reported in various articles. Farm types are described in [Fayama et al., 2018](https://www.researchgate.net/publication/336023108_An_analysis_of_the_trajectories_and_intensification_paths_of_polyculture-livestock_farms_in_a_context_of_social_change_in_western_Burkina_Faso_and_northern_Cote_d'Ivoire_Une_analyse_des_trajectoires_e) and [Ouédraogo et al. 2016 (requires a Cirad account)](https://agris.fao.org/agris-search/search.do?recordID=FR2019153347).

###  [Q1]. Are observed farm types and trajectories predicted by the model?

#### Are observed farm types predicted by the model, and under which scenarios?

###### Separating (splitting) states belonging to each farm type

To answer this question, we rely on previously defined farm types (A1, A2, A3, AP, B). These farm types are state properties, i.e. they are defined at the state level based on present-absent variables. 

We split the symbolic STG based on these state properties such that states sharing the same farm type are grouped together. This technique, known as **summary graph**, is equivalent to what has been done in previous studies ([Cosme et al., 2021](https://www.mdpi.com/2073-445X/11/1/42)) using explicit STGs, and is borrowed from [Diop et al., 2019](https://hal.inria.fr/hal-02737659).

In [4]:
# Splits the STG according to farm types and exhibit transitions between them.
farm_types_graph = STG.split(**farm_types)
farm_types_graph = farm_types_graph.draw(nodes_label="EQUALS", edges_label = "", layout = "circle",  
                                         nodes_label_size = 20, nodes_size = 50, nodes_fill_palette = "white", 
                                         nodes_draw_color = "black", nodes_draw_width = 0.5,
                                         edges_curve = "straight",edges_draw_width = 1, edges_tip_scale = 1)
# Shows the STG whose nodes gather all farm states belonging to the same farm type 
farm_types_graph

This graph summarizes transitions between each farm type. 

##### Visualization, analysis and export

To get details on graph visualization options, type `?g` (with `g` the graph you just built, in our case `farm_types_graph`) and run cell.  

The list of color palettes can be found at `Palette.palettes`.

To download figures, (1) open the "Export" menu at the bottom of the figure, (2) place your mouse on each node until the progress (captured) bar il full, (3) choose the output format (PNG, PDF, TikZ or LaTeX) and (4) click "export". 

Each node can be inspected by clicking on it and opening the "Inspector" menu.

All empirically-observed farm types are reachable by A1 farmers (which is the initial state in the model), and are thus predicted by the model. Therefore, data on farm types do not falsify the model.

#### Under which scenarios (i.e. from which initial states) are observed farm types predicted by the model ?

This question is **temporal** by nature. Indeed, each scenario corresponds to a distinct set of initial states. Therefore, this question can be reinterpreted as "from which initial states is that farm type reachable?". 

For that purpose, we will need a [temporal logic](https://fr.wikipedia.org/wiki/Logique_temporelle#:~:text=Signal%20Temporal%20Logic%20(STL)%20qui,que%20les%20r%C3%A9sultats%20par%20Y.), and more specifically [CTL](https://en.wikipedia.org/wiki/Computation_tree_logic).

For each farm type, we defined a reachability formula in CTL language of the form $\exists F(farm type)$.

In [5]:
reach_A1 = f"(EF{A1})"
reach_A2 = f"(EF{A2})"
reach_A3 = f"(EF{A3})"
reach_AP = f"(EF{AP})"
reach_B = f"(EF{B})"

Then, we split the symbolic STG based on two criteria: (1) farm type and (2) initial state. Note that all initial states have the farm type A1. 

In [6]:
farmtypes = STG.split("INIT", reach_A1, reach_A2, reach_A3, reach_AP, reach_B)

This STG split provides sets of states. Based on these sets, we identify those being (1) initial states and (2) leading to the farm type of interest. 

A scenario is defined as a combination of control variables. Therefore, our answer will take the form of a list of control variables.

More specifically, our result will be a Boolean expression (as it can be read as "this farm type is reachable from this scenario OR this scenario OR this scenario", and so on). This Boolean expression will then be simplified into a canonical form (here, we chose a Disjunctive Normal Form, or "OR of ANDs"). 

In [7]:
# Control variables used for defining scenarios
controls = ["EC", "Nf", "CRC", "Rg", "Fg", "Flw", "Lv"]
# Identifying initial states (scenarios) from which farm types are reachable? 
# "dnf": results are described as a boolean expression which is put into a canonical form (here, a Disjunctive Normal Form (DNF))
display(
    farmtypes.form(*(farmtypes.isin(reach_A1) & farmtypes.isin("INIT")), variables=controls, normalise="dnf"),
    farmtypes.form(*(farmtypes.isin(reach_A2) & farmtypes.isin("INIT")), variables=controls, normalise="dnf"),
    farmtypes.form(*(farmtypes.isin(reach_A3) & farmtypes.isin("INIT")), variables=controls, normalise="dnf"),
    farmtypes.form(*(farmtypes.isin(reach_AP) & farmtypes.isin("INIT")), variables=controls, normalise="dnf"),
    farmtypes.form(*(farmtypes.isin(reach_B)  & farmtypes.isin("INIT")), variables=controls, normalise="dnf")
)

True

(Fg & Nf) | (Nf & ~Flw) | (CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg)

(Fg & Nf) | (Nf & ~Flw) | (CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg)

(Fg & Nf) | (Nf & ~Flw) | (CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg)

(Fg & Nf) | (Nf & ~Flw) | (CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg)

As these variables are controls, each parenthesis (i.e. each "AND") is a scenario or, more rigorously, a group of scenarios able to lead to the farm type of interest. Indeed, the scenario **(𝐹𝑔 $\land$ 𝑁𝑓)** only specifies the value of these two control variables and leaves the other variables unspecified.

###### Answer 
The $A1$ farm type is reachable under all scenarios (the property $\exists F (A1)$ is true for all states), which is trivial as all initial states are $A1$.


All other farm types ($A2$, $A3$, $AP$ and $B$) are reachable under:

**(𝐹𝑔 $\land$ 𝑁𝑓) $\lor$ (𝑁𝑓 $\land$ 𝐹𝑙𝑤-) $\lor$ (𝐶𝑅𝐶 $\land$ 𝐹𝑙𝑤 $\land$ 𝐿𝑣) $\lor$ (𝐶𝑅𝐶 $\land$ 𝐿𝑣 $\land$ 𝑅𝑔) $\lor$ (𝐹𝑔 $\land$ 𝐹𝑙𝑤 $\land$ 𝐿𝑣) $\lor$ (𝐹𝑔 $\land$ 𝐿𝑣 $\land$ 𝑅𝑔)**.

Or, put into a more compact form : 

**[Lv $\land$ (Flw $\lor$ Rg) $\land$ (CRC $\lor$ Fg)] $\lor$ [Nf $\land$ (Flw− $\lor$ Fg)]**

Therefore, A2, A3, AP and B are reachable:

1. if  livestock is initially present with sufficient fodder in rainy season (fallows or rangelands) and dry season (collected residues or residues grazed during free grazing on other fields) 

or 

2. if the farm practices non-farm activities and does not practice fallowing or allows free grazing.

#### Are observed farm transitions and trajectories predicted by the model, and under which scenarios?

Now, we define observed farm transitions and trajectories described in the "Farm trajectories" section of "Material and Methods" and taken from [Fayama et al., 2018](https://www.researchgate.net/publication/336023108_An_analysis_of_the_trajectories_and_intensification_paths_of_polyculture-livestock_farms_in_a_context_of_social_change_in_western_Burkina_Faso_and_northern_Cote_d'Ivoire_Une_analyse_des_trajectoires_e) and [Ouédraogo et al. 2016 (requires a Cirad account)](https://agris.fao.org/agris-search/search.do?recordID=FR2019153347).

###### Observed farm transitions 

| Farm transition     | CTL formula &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; |
|:--------------------|:------------------------------------------------------|
| $A1 \rightarrow A2$ | $A1 \land \exists(A1\ U\ A2)$ |
| $A2 \rightarrow A3$ | $A2 \land \exists(A2\ U\ A3)$ |
| $A3 \rightarrow AP$ | $A3 \land \exists(A3\ U\ AP)$ |
| $B \rightarrow AP$  | $B \land \exists(B\ U\ AP)$  |
| $A2 \rightarrow A1$ | $A2 \land \exists(A2\ U\ A1)$ | 

with logical ($\land$), branching ($\exists$) and temporal ($U$) operators defined in the main text.

###### Observed farm trajectories 

| Farm trajectory &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; | CTL formula &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; &nbsp; |
|:--------------------|:---------------------------------|
| $A1\rightarrow A2\rightarrow A3\rightarrow AP$ | $A1 \land \exists(A1\ U\ (A2 \land (\exists(A2\ U\ (A3 \land (\exists(A3\ U\ AP)))))))$ 	|
| $A1 \land A1 \rightarrow A2 \rightarrow AP$ | $\exists(A1\ U\ (A2 \land (\exists(A2\ U\ AP))))$|


with logical ($\land$), branching ($\exists$) and temporal ($U$) operators defined in the main text.

###### Defining farm transitions and trajectories

In [8]:
# Farm transitions
A1_A2 = f"(E({A1} U {A2}))" # A1 -> A2
A2_A3 = f"(E({A2} U {A3}))" # A2 -> A3
A3_AP = f"(E({A3} U {AP}))" # A3 -> AP
B_AP = f"(E({B}  U {AP}))" # B -> AP
A2_A1 = f"(E({A2} U {A1}))" # A2 -> A1
# Farm trajectories
A1_A2_A3_AP =  f"E({A1} U ({A2} & (E({A2} U ({A3} & (E({A3} U {AP})))))))" # A1 -> A2 -> A3 -> AP
A1_A2_AP =  f"E({A1} U ({A2} & (E({A2} U {AP}))))" # A1 -> A2 -> AP

##### Farm transitions

###### Separating (splitting) states verifying each farm transition (i.e. from which the transition is possible)

In [9]:
# Separating states verifying the farm transitions defined previously
farm_transitions = STG.split(A1_A2, A2_A3, A3_AP, B_AP, A2_A1)

###### Question 
Are observed farm transitions predicted by the model ?

In [10]:
display(
    bool(farm_transitions.isin(A1_A2)), # Is A1 -> A2 predicted ?
    bool(farm_transitions.isin(A2_A3)), # Is A2 -> A3 predicted ?
    bool(farm_transitions.isin(A3_AP)), # Is A3 -> AP predicted ?
    bool(farm_transitions.isin(B_AP)),  # Is B  -> AP predicted ?
    bool(farm_transitions.isin(A2_A1))  # Is A2 -> A1 predicted ?
)

True

True

True

True

True

###### Answer 

Yes, farm transitions $A1 \rightarrow A2$, $A2 \rightarrow A3$, $A3 \rightarrow AP$, $B \rightarrow AP$ and $A2 \rightarrow A1$ are predicted by the model.


###### Question 
Under which scenarios are observed farm transitions predicted?

In [11]:
# Control variables used for defining scenarios
controls = ["EC", "Nf", "CRC", "Rg", "Fg", "Flw", "Lv"]
# Identifying initial states (scenarios) for which farm transitions are possible? 
# "dnf": results are described as a boolean expression which is put into a canonical form (here, a Disjunctive Normal Form (DNF))
display(
    farm_transitions.form(*(farm_transitions.isin(A1) & farm_transitions.isin(A1_A2)), variables=controls, normalise="dnf"), # What are the scenarios in which an A1 farm can directly shift to A2?
    farm_transitions.form(*(farm_transitions.isin(A2) & farm_transitions.isin(A2_A3)), variables=controls, normalise="dnf"), # What are the scenarios in which an A2 farm can directly shift to A3?
    farm_transitions.form(*(farm_transitions.isin(A3) & farm_transitions.isin(A3_AP)), variables=controls, normalise="dnf"), # What are the scenarios in which an A3 farm can directly shift to AP?
    farm_transitions.form(*(farm_transitions.isin(B)  & farm_transitions.isin(B_AP)),  variables=controls, normalise="dnf"), # What are the scenarios in which an B farm can directly shift to AP?
    farm_transitions.form(*(farm_transitions.isin(A2) & farm_transitions.isin(A2_A1)), variables=controls, normalise="dnf")  # What are the scenarios in which an A2 farm can directly shift to A1?
)

True

(CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg) | (Lv & Nf & ~Flw)

(CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg) | (Lv & Nf & ~Flw)

(CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg) | (Lv & Nf & ~Flw)

(CRC & Lv & Nf & ~Flw) | (CRC & Lv & Rg & ~Flw) | (Fg & Lv & Nf & ~Flw) | (Fg & Lv & Rg & ~Flw) | (Lv & Nf & ~EC & ~Flw)

###### Answer
The $A1 \rightarrow A2$ transition is possible in scenarios: $(𝐶𝑅𝐶 \land 𝐹𝑙𝑤 \land 𝐿𝑣) \lor (𝐶𝑅𝐶 \land 𝐿𝑣 \land 𝑅𝑔) \lor (𝐹𝑔 \land 𝐹𝑙𝑤 \land 𝐿𝑣) \lor (𝐹𝑔 \land 𝐿𝑣 \land 𝑅𝑔) \lor (𝐿𝑣 \land 𝑁𝑓 \land 𝐹𝑙𝑤-)$.

Or, into a more compact form: ``Lv, [(CRC|Fg, Flw|Rg) | (Nf, Flw-]``.

(The property $\exists F (A1)$ is true for all states), which is trivial as all initial states are `A1`.)

All other farm types (`A2`, `A3`, `AP` and `B`) are reachable under:

$(𝐹𝑔 \land 𝑁𝑓) \lor (𝑁𝑓 \land 𝐹𝑙𝑤-) \lor (𝐶𝑅𝐶 \land 𝐹𝑙𝑤 \land 𝐿𝑣) \lor (𝐶𝑅𝐶 \land 𝐿𝑣 \land 𝑅𝑔) \lor (𝐹𝑔 \land 𝐹𝑙𝑤 \land 𝐿𝑣) \lor (𝐹𝑔 \land 𝐿𝑣 \land 𝑅𝑔)$.

Or, put into a more compact form : `[Lv, (Flw|Rg), (CRC|Fg)] | [Nf, (Flw−|Fg)]`

##### Farm trajectories

###### Separating (splitting) states verifying each  farm trajectory (i.e. from which the trajectory is possible)

In [12]:
# Separating states verifying the farm transitions defined previously
farm_trajectories = STG.split("INIT", A1_A2_A3_AP, A1_A2_AP)

###### Question 
Are observed farm trajectories predicted by the model ?

In [13]:
display(
    bool(farm_trajectories.isin(A1_A2_A3_AP)), # Is A1 -> A2 -> A3 -> AP predicted ?
    bool(farm_trajectories.isin(A1_A2_AP)) # Is A1 -> A2 -> AP predicted ?
)

True

True

###### Answer
Yes, farm trajectories $A1\rightarrow A2\rightarrow A3\rightarrow AP$ and $A1\rightarrow A2\rightarrow AP$ are predicted by the model.

###### Question 
Under which scenarios are observed farm trajectories predicted?

In [14]:
# Control variables used for defining scenarios
controls = ["EC", "Nf", "CRC", "Rg", "Fg", "Flw", "Lv"]

# Identifying initial states (scenarios) for which farm transitions are possible? 
# "dnf": results are described as a boolean expression which is put into a canonical form (here, a Disjunctive Normal Form (DNF))
display(
    farm_trajectories.form(*(farm_trajectories.isin(A1) & farm_trajectories.isin(A1_A2_A3_AP)), variables=controls, normalise="dnf"), # What are the scenarios in which an A1 farm can directly shift to A2, and then directly A3 and directly AP?
    farm_trajectories.form(*(farm_trajectories.isin(A1) & farm_trajectories.isin(A1_A2_AP)), variables=controls, normalise="dnf") # What are the scenarios in which an A1 farm can directly shift to A2, and then directly AP?
)

(Fg & Nf) | (Nf & ~Flw) | (CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg)

(Fg & Nf) | (Nf & ~Flw) | (CRC & Flw & Lv) | (CRC & Lv & Rg) | (Fg & Flw & Lv) | (Fg & Lv & Rg)

###### Answer

As for reaching A2, A3 or AP from A1, these two trajectories are possible under scenarios `[Lv, (Flw|Rg), (CRC|Fg)] | [Nf, (Flw−|Fg)]`.

### Details

**What are the values of variables for states verifying $A1 \land E(A1 U A2)$ (with/without livestock)?**

For controls: 
- Possible:
    - Flw, CRC, Lv
    - Rg, CRC, Lv
    - Flw, Fg, Lv
    - Rg, Fg, Lv
    - Flw-, Nf
    - Fg, Nf
    - Summary: 
        - `Lv, (Flw|Rg), (CRC|Fg) `
        - `Nf, (Flw-|Fg)`
- Impossible:
    - Fg-, CRC- (no food during dry season)
    - Fg-, Lv- 
    - Nf-, Lv- (no capital)
    - Flw- 
    - Summary: 
        - `Lv-, Fg-|Nf- `
        - `Fg-, CRC-`
        - `Flw-`
For state variables:
- Possible:
    - Cr, Fe, Lv
    - Cr, Fe, Eq-
- Impossible:
    - Lv, Fe-
    - Eq-, Fe-
    - Cr, Eq-, Fc-
    - Cr, Eq-, Lv-

**What are the values of variables for states verifying $A2 \land \exists(A2 U A3)$ or $A3 \land \exists(A3 U AP)$ or $A3 \land \exists(A3 U AP)$ or $P \land \exists(P U AP)$?**

For controls, verifying: 
   - Flw, CRC
   - Rg, CRC
   - Flw, Fg
   - Rg, Fg
   - Flw-, Nf
   - Summary: `(Flw|Rg , CRC|Fg) | (Flw-, Nf)`
        
Not verifying:
   - Flw-, Nf, EC-
   - Flw-, Nf, CRC
   - Flw-, Nf, Fg
   - Flw-, Rg, CRC
   - Flw, Rg, Fg
   - Summary: `Flw-, (Rg|Nf, CRC|Fg) | (Nf, EC-)`
    
Except $P \land \exists(P U AP)$, not verifying : 
   - Flw-, Rg, CRC
   - Flw-, Rg, Fg
   - Flw-, Nf
   - Sumary: 
       - `Flw-, Rg, CRC|Fg`
       - `Flw-, Nf`

**What are the values of variables for states verifying $A2 \land E(A2 U A1)$?**

For controls: 
- Possible 
    - Flw-, Nf, EC- 
    - Flw-, Nf, CRC 
    - Flw-, Rg, CRC 
    - Flw-, Nf, Fg 
    - Flw-, Rg, Fg 
    - Résumé : Flw-, ((Nf|Rg),(CRC|Fg)) | (Nf,EC-)
    
    
- Impossible :
    - Flw, CRC
    - Flw, Fg
    - Flw-, Nf, Fg-, CRC-, EC
    - Résumé : 
        - Flw, CRC|Fg
        - Flw-, CRC-, Fg-, Nf, EC
   

For state variables:
- Possible 
    - Fe-, Cr

- Impossible 
    - Fe, Cr

**Values of control variables for each trajectory to be possible or impossible:**

Possible : 
- **A1 & E(A1 U A2)**: `Lv, (Flw|Rg), (CRC|Fg)` OR `Nf, (Flw-|Fg)`
- **A2 & E(A2 U A3)**: `(Flw|Rg), (CRC|Fg)` OR `Flw-, Nf`
- **A3 & E(A3 U AP)**: `(Flw|Rg), (CRC|Fg)` OR `Flw-, Nf`
- **P  & E(P  U AP)**: `(Flw|Rg), (CRC|Fg)` OR `Flw-, Nf`
- **A2 & E(A2 U A1)**: `Flw-, (Rg|Nf), (CRC|Fg)` OR `Flw-, Nf, EC-`

Impossible: 
- **A1 & E(A1 U A2)**: `Fg-, CRC-` OR `Flw-` OR `Lv-, Fg-|Nf-`
- **A2 & E(A2 U A3)**: `Flw-, (Rg|Nf), (CRC|Fg)` OR `Flw-, Nf, EC-`
- **A3 & E(A3 U AP)**: `Flw-, (Rg|Nf), (CRC|Fg)` OR `Flw-, Nf, EC-`
- **P  & E(P  U AP)**: `Flw-, Rg, CRC|Fg` OR `Flw-, Nf`
- **A2 & E(A2 U A1)**: `Flw, CRC|Fg` OR `Flw-, CRC-, Fg-, Nf, EC`

**Trajectory A1>A2>A3 realized**
- `406` -R30,R31-> `333` -R20-> `327` -(R13, R14, R15, R16, R17)-> `319`
- `406` -R30,R31-> `334` -R20-> `327` -(R13, R14, R15, R16, R17)-> `319`

**THUS** `A1 -Eq+-> A2 -Cc+-> A3 -Ma+-> AP`

**Scenarios that diverge from the trajectory:**
- A1 -(Ma+)-> P
- A1 -(Fe-)-> A1 -(Ma+)-> P
- A2 -(Ma+)-> P/transient
- A2 -(Fe-)-> A2 -(Ca-, Eq-, Lv-, Ma-)-> A1 
- A3 -(Fe-)-> A3 -(Cc-)-> A2
- A3 -(Fe-)-> A3 -(Ca-, Cr-, Eq-, Lv-, Ma-)--> transient

THUS `A1 > Ma+|Fe-` OR `A2 > Ma+|Fe-` OR `A3 > Fe-` because `Fe-` indirectly causes the disapearing of either cash crop farming, either residues and fodder crops, livestock disappearing if management conditions require it.

**What are the values of variables for states verifying $A1 > A2 > A3$ (without livestock)?**

**For controls (initial states):** 
- Possible:
    - Flw- 
    - Fg, Nf
- Impossible:
    - Flw, Fg-
    - Flw, Nf-
    
**For controls (all states):**
- Possible:
    - Flw- 
    - Fg, Nf
- Impossible:
    - Fg-
    - Nf-
    - Flw-
    
NB: In the general case (not focusing on initial states), controls do not allow to discriminate states verifying the trajectory from those which do not. Therefore, state variables play the major role in this case.

**What are the values of variables for states verifying $A1 \land E(A1 U (A2 \land E(A2 U AP)))$ (without livestock)?**

**For controls (initial states):** 
- Possible 
    - Flw- 
    - Fg, Nf
    
- Impossible :
    - Flw, Fg-
    - Flw, Nf-
    
**For controls (all states):**
- Possible 
    - Flw- 
    - Fg, Nf
    
- Impossible :
    - Fg-
    - Nf-
    - Flw-
    
NB: In the general case (not focusing on initial states), controls do not allow to discriminate states verifying the trajectory from those which do not. Therefore, state variables play the major role in this case.

###### Summary:

- `A1 > A2 > A3 > AP` is possible from `Flw-` or `Fg, Nf`
- `A1 > A2 > AP` is possible from `Flw-` or `Fg, Nf`

## How (not) to reach a persistent agropastoralism?

In [15]:
f1 = f"AG({AP})" # persistent_agropastoralism
f2 = f"(EFAG({AP}))" # AP possible
f3 = f"~(EF(AG(~({AP}))))" # AP impossible

In [16]:
# Splits the STG according to farm types and exhibit transitions between them.
reach_persistent_AP = STG.split(f1, f2, f3, "INIT")
reach_persistent_AP_graph = reach_persistent_AP.draw(nodes_label="EQUALS", edges_label = "", layout = "dagre",  
                                         nodes_label_size = 20, nodes_size = 50, nodes_fill_palette = "white", 
                                         nodes_draw_color = "black", nodes_draw_width = 0.5,
                                         edges_curve = "straight",edges_draw_width = 1, edges_tip_scale = 1)
# Shows the STG whose nodes gather all farm states belonging to the same farm type 
reach_persistent_AP_graph

In [17]:
controls = ["EC", "Nf", "CRC", "Flw", "Rg", "Fg", "Lv"]
statevar = ["Cr", "Fe", "Fp", "Eq", "Ma", "Ca", "Lv", "Cc"]
# Necessary
# Possible
# Impossible
display(
    reach_persistent_AP.form(*(reach_persistent_AP.isin(f2) & reach_persistent_AP.isin(f3) & reach_persistent_AP.isin("INIT")), variables=controls, normalise="dnf"),
    reach_persistent_AP.form(*(reach_persistent_AP.isin(f2) & reach_persistent_AP.hasno(f3) & reach_persistent_AP.isin("INIT")), variables=controls, normalise="dnf"),
    reach_persistent_AP.form(*(reach_persistent_AP.hasno(f2) & reach_persistent_AP.isin("INIT")), variables=controls, normalise="dnf"),
)

(CRC & Flw & Lv) | (Fg & Flw & Lv) | (Fg & Flw & Nf)

(EC & Nf & ~Flw) | (CRC & EC & Lv & Rg & ~Flw) | (EC & Fg & Lv & Rg & ~Flw)

(~EC & ~Flw) | (~Lv & ~Nf) | (Flw & ~CRC & ~Fg) | (Flw & ~Fg & ~Lv) | (~CRC & ~Fg & ~Nf) | (~Flw & ~Nf & ~Rg)

- Scenarios in which persistent AP is necessarily reached : `(CRC,Flw,Lv) | (Fg,Flw,Lv) | (Flw,Fg,Nf)`
- Scenarios in which persistent AP not necessarily reachable  : `(EC,Nf,Flw-) | (CRC,EC,Lv,Rg,Flw-) | (EC,Fg,Lv,Rg,Flw-)`
- Scenarios in which persistent AP is unreachable : `(EC-,Flw-) | (Lv-,Nf-) | (Flw,CRC-,Fg-) | (Flw,Fg-,Lv-) | (CRC-,Fg-,Nf-) | (Flw-,Nf-,Rg-)`